# Central Hidroeléctrica Yacyretá
## 09J - Test de Causalidad de Granger
### Variables exógenas con selección por Granger Test. Loopeado para varios fh y lags, que se configuran, asi como los regresores a usar.
#### Fecha: 21-Enero-22

In [1]:
# Para que funcione más rápidamente el intellisense
#%config Completer.use_jedi = False

In [2]:
#Cargo numpy y pandas para trabajar con dataframes
import pandas as pd
import numpy as np
from datetime import date, timedelta, datetime

import matplotlib.pyplot as plt
plt.rcParams['figure.figsize'] = (16, 6)

In [3]:
# Imports necesarios para que funcione iplot() como método de pandas
%matplotlib inline
import plotly.graph_objs as go
from  plotly.offline import plot
import chart_studio.plotly as py
import cufflinks as cf
cf.go_offline()
from plotly.offline import download_plotlyjs, init_notebook_mode, plot,iplot
init_notebook_mode(connected='true')

In [4]:
# Planto una semilla para repetitibilidad
import random
random.seed(170162)
np.random.seed(170162)

In [1]:
import pprint
from tabulate import tabulate

In [6]:
from sktime.utils.plotting import plot_series
from sklearn.base import clone

In [7]:
# Importo los regresores
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.linear_model import LinearRegression
from sklearn.svm import SVR
from lightgbm import LGBMRegressor
from sklearn.neural_network import MLPRegressor
from sklearn.linear_model import Lasso, Ridge  

In [8]:
# Métricas de evaluación de desempeño
from sktime.performance_metrics.forecasting import MeanAbsoluteError, MeanSquaredError, MeanAbsoluteScaledError

### Carpeta para los archivos '.csv' y gráficos

#### Nombre del Experimento

In [9]:
experimento = 'TFI 09J - Multivariable with Granger Causality, random_state'

In [10]:
ahora = str(datetime.now()).replace(':', '-').replace(' ', '_')[:16]
path_grabacion = './output/' + experimento + '/'+ ahora + '/'
# Verifico que la carpeta exista y si no, la creo
import os
if not os.path.exists(path_grabacion):
    os.makedirs(path_grabacion)
    print('\nPath/carpeta de gráficos y de archivos creada:', path_grabacion)


Path/carpeta de gráficos y de archivos creada: ./output/TFI 09J - Multivariable with Granger Causality, random_state/2022-06-04_13-50/


### Lectura del Dataset de la central hidroeléctrica Yacyretá

In [11]:
# Especifico el nombre del archivo con el dataset unificado de la CHY y el path
path = './datasets/CHY/output/'
file_name = 'CHY_dataset.csv'

In [12]:
# Leo el dataset creado en el notebook anterior
df = pd.read_csv(path + file_name)

In [13]:
# veo cabeza y cola del df
df

FECHA  COTA_EMBALSE  COTA_RESTITUCION  SALTO    QAFLR  QVBP  \
0     2011-01-01         82.04             60.17  21.87  13936.0   0.0   
1     2011-01-02         82.06             60.17  21.89  13267.0   0.0   
2     2011-01-03         82.07             60.12  21.95  12670.0   0.0   
3     2011-01-04         82.08             60.12  21.96  12909.0   0.0   
4     2011-01-05         82.13             60.08  22.05  13787.0   0.0   
...          ...           ...               ...    ...      ...   ...   
3828  2021-06-26         82.78             58.94  23.84   6545.0   0.0   
3829  2021-06-27         82.78             58.94  23.84   6337.0   0.0   
3830  2021-06-28         82.79             58.93  23.86   6138.0   0.0   
3831  2021-06-29         82.79             58.93  23.86   6133.0   0.0   
3832  2021-06-30         82.82             58.93  23.89   6151.0   0.0   

       QVBAC    QTURB     SINP       SADI  
0     1045.0  11977.0  5391.00  49384.000  
1     1045.0  11863.0  5631.60  48785.000  
2     1045.0  11439.0  6871.60  46573.000  
3     1045.0  11505.0  7460.80  46046.000  
4     1047.0  11455.0  6555.00  46721.000  
...      ...      ...      ...        ...  
3828  1017.0   5157.0  4388.60  21594.112  
3829  1017.0   5135.0  4188.42  21658.536  
3830  1017.0   5121.0  5165.92  20606.040  
3831  1017.0   5116.0  5427.90  20416.960  
3832  1017.0   5134.0  5466.60  20409.920  

[3833 rows x 10 columns]

In [14]:
# Convierto la columna FECHA de object a datetime64
df['FECHA'] = pd.to_datetime(df['FECHA'])

In [15]:
# Hago que la columna FECHA sea el índice
df.set_index('FECHA', inplace=True)

In [16]:
# Si fuera necesario imputar NAN
df = df.asfreq('D', method='ffill')

### Copio el df

In [17]:
ds = df.copy()

In [18]:
features_exogenas = [col for col in ds.columns if col != 'SALTO']
features_exogenas

['COTA_EMBALSE',
 'COTA_RESTITUCION',
 'QAFLR',
 'QVBP',
 'QVBAC',
 'QTURB',
 'SINP',
 'SADI']

### Ads Test for Stationarity

In [19]:
from statsmodels.tsa.stattools import adfuller

# Null hypothesis: If failed to be rejected, it suggests the time series is not stationarity.
# Alternative hypothesis: The null hypothesis is rejected, it suggests the time series is stationary.

def adf_test(ds):
    result = adfuller(ds.values)
    print('Ads Statistics: %f' % result[0])
    print('p-value: %f' % result[1])
    print('Critical values:')
    for key, value in result[4].items():
        print('\t%s: %.3f' % (key, value))

In [20]:
# Test sobre la variable SALTO
adf_test(ds['SALTO'])

Ads Statistics: -5.442622
p-value: 0.000003
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567


In [21]:
# Test sobre las variables
for feature in features_exogenas:
    print('\nTest de Ads sobre:', feature)
    adf_test(ds[feature])


Test de Ads sobre: COTA_EMBALSE
Ads Statistics: -4.578956
p-value: 0.000141
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: COTA_RESTITUCION
Ads Statistics: -4.419289
p-value: 0.000274
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: QAFLR
Ads Statistics: -5.030431
p-value: 0.000019
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: QVBP
Ads Statistics: -8.599323
p-value: 0.000000
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: QVBAC
Ads Statistics: -6.347403
p-value: 0.000000
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: QTURB
Ads Statistics: -3.408536
p-value: 0.010671
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: SINP
Ads Statistics: -4.176139
p-value: 0.000723
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: SADI
Ads Statistics: -4.374439
p-value: 0.000329
Critical values:
	1%: -3.432
	5%: -2.862
	10%: 

### KPSS Test for Stationary

In [22]:
from statsmodels.tsa.stattools import kpss

# Null hypothesis: The time series is stationary
# Alternative hypothesis: The time series is not stationary

def kpss_test(ds):    
    statistic, p_value, n_lags, critical_values = kpss(ds.values)
    
    print(f'KPSS Statistic: {statistic}')
    print(f'p-value: {p_value}')
    print(f'num lags: {n_lags}')
    print('Critial Values:')
    for key, value in critical_values.items():
        print(f'   {key} : {value}')

In [23]:
# Test sobre la variable SALTO
kpss_test(ds['SALTO'])

KPSS Statistic: 1.141461271212905
p-value: 0.01
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739


C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1850: FutureWarning:

The behavior of using nlags=None will change in release 0.13.Currently nlags=None is the same as nlags="legacy", and so a sample-size lag length is used. After the next release, the default will change to be the same as nlags="auto" which uses an automatic lag length selection method. To silence this warning, either use "auto" or "legacy"

C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1881: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.




In [24]:
# Test sobre las variables
for feature in features_exogenas:
    print('\nTest de Ads sobre:', feature)
    kpss_test(ds[feature])


Test de Ads sobre: COTA_EMBALSE
KPSS Statistic: 4.8982908572459625
p-value: 0.01
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739

Test de Ads sobre: COTA_RESTITUCION
KPSS Statistic: 3.5659095524700346
p-value: 0.01
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739

Test de Ads sobre: QAFLR
KPSS Statistic: 3.096764794859414
p-value: 0.01
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739

Test de Ads sobre: QVBP
KPSS Statistic: 0.3776503035039445
p-value: 0.08678866228278254
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739

Test de Ads sobre: QVBAC
KPSS Statistic: 1.9280577869751787
p-value: 0.01
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739

Test de Ads sobre: QTURB
KPSS Statistic: 4.291792415276011
p-value: 0.01
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% 

C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1881: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.


C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1881: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.


C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1881: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.


C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1881: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the 

In [25]:
# Diferencio las features 
for col in ds.columns:
    ds[col+'_diff'] = ds[col].diff()

####  Borro los registros que quedaron con un NAN al desplazarse

In [26]:
ds.dropna(how='any', inplace=True)

In [27]:
# Coloco las variables diferenciadas en una lista
features_exogenas_diff = [col for col in ds.columns if (col[0:5]!='SALTO')  and (col[-4:-1] == 'dif')]

In [28]:
features_exogenas_diff

['COTA_EMBALSE_diff',
 'COTA_RESTITUCION_diff',
 'QAFLR_diff',
 'QVBP_diff',
 'QVBAC_diff',
 'QTURB_diff',
 'SINP_diff',
 'SADI_diff']

### Ads Test for Stationarity, sobre las series diferenciadas

In [29]:
# Test sobre la variable SALTO
adf_test(ds['SALTO_diff'])

Ads Statistics: -14.557922
p-value: 0.000000
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567


In [30]:
# Test sobre las variables
for feature in features_exogenas_diff:
    print('\nTest de Ads sobre:', feature)
    adf_test(ds[feature])


Test de Ads sobre: COTA_EMBALSE_diff
Ads Statistics: -13.427363
p-value: 0.000000
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: COTA_RESTITUCION_diff
Ads Statistics: -14.729156
p-value: 0.000000
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: QAFLR_diff
Ads Statistics: -14.207630
p-value: 0.000000
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: QVBP_diff
Ads Statistics: -17.182967
p-value: 0.000000
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: QVBAC_diff
Ads Statistics: -14.251566
p-value: 0.000000
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: QTURB_diff
Ads Statistics: -14.248722
p-value: 0.000000
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: SINP_diff
Ads Statistics: -14.519805
p-value: 0.000000
Critical values:
	1%: -3.432
	5%: -2.862
	10%: -2.567

Test de Ads sobre: SADI_diff
Ads Statistics: -13.894742
p-value: 0.000000

### KPSS Test for Stationary

In [31]:
# Null hypothesis: The time series is stationary
# Alternative hypothesis: The time series is not stationary

In [32]:
# Test sobre la variable SALTO
kpss_test(ds['SALTO_diff'])

KPSS Statistic: 0.015555882849060695
p-value: 0.1
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739


C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1850: FutureWarning:

The behavior of using nlags=None will change in release 0.13.Currently nlags=None is the same as nlags="legacy", and so a sample-size lag length is used. After the next release, the default will change to be the same as nlags="auto" which uses an automatic lag length selection method. To silence this warning, either use "auto" or "legacy"

C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1885: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.




In [33]:
# Test sobre las variables
for feature in features_exogenas_diff:
    print('\nTest de Ads sobre:', feature)
    kpss_test(ds[feature])


Test de Ads sobre: COTA_EMBALSE_diff
KPSS Statistic: 0.17198848484133672
p-value: 0.1
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739

Test de Ads sobre: COTA_RESTITUCION_diff
KPSS Statistic: 0.018606973249691523
p-value: 0.1
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739

Test de Ads sobre: QAFLR_diff
KPSS Statistic: 0.012195425397892472
p-value: 0.1
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739

Test de Ads sobre: QVBP_diff
KPSS Statistic: 0.004760177645989472
p-value: 0.1
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739

Test de Ads sobre: QVBAC_diff
KPSS Statistic: 0.008574942052431905
p-value: 0.1
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463
   2.5% : 0.574
   1% : 0.739

Test de Ads sobre: QTURB_diff
KPSS Statistic: 0.031113450384536615
p-value: 0.1
num lags: 30
Critial Values:
   10% : 0.347
   5% : 0.463


C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1885: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1885: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1885: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


C:\Users\josel\.conda\envs\tesis\lib\site-packages\statsmodels\tsa\stattools.py:1885: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

### Granger Test

In [34]:
# Importo la función de test de Granger Causality
from statsmodels.tsa.stattools import grangercausalitytests

In [35]:
selectedLaggedfeatures=[]
for feature in features_exogenas_diff:
    # Analizo hasta el 21avo lag de cada variable
    grangerResults=grangercausalitytests(ds[['SALTO_diff', feature]], maxlag=21, verbose=False)
    print('pValue                           FValue')
    fValue = j = 0
    for i in range(1, 21+1):
        print(i, grangerResults[i][0]['ssr_ftest'][1], ' - ', grangerResults[i][0]['ssr_ftest'][0])
        if grangerResults[i][0]['ssr_ftest'][1] < .05:
            if grangerResults[i][0]['ssr_ftest'][0] > fValue:
                j = i
                fValue = grangerResults[i][0]['ssr_ftest'][0]
    print('Selected feature: ', feature, ' lag: ', j, '\n')
    selectedLaggedfeatures.append([feature, j])

pValue                           FValue
1 1.7831383979342623e-47  -  215.345537832426
2 2.500153078956832e-42  -  98.23112674444708
3 1.8078942157916457e-46  -  73.91641717020153
4 4.7837231779723306e-52  -  63.5007151123419
5 4.5718408121753136e-51  -  50.73811898380943
6 9.360546688538057e-52  -  43.57356973448945
7 1.4185619971183956e-49  -  36.37906602961886
8 2.8685627979659714e-48  -  31.504372990786038
9 2.2499822414135424e-48  -  28.485227191126885
10 1.7695785370695323e-49  -  26.567057098772516
11 1.1249061418038416e-49  -  24.573154921568996
12 4.108868176328835e-49  -  22.581383800482186
13 2.916007289014292e-48  -  20.774585588344774
14 1.55022239512092e-48  -  19.6336923578136
15 6.721627063787914e-48  -  18.32678097334115
16 1.262111681318129e-47  -  17.296409965432392
17 3.1479327568286795e-48  -  16.65307578082849
18 4.89978467710165e-48  -  15.84833295557788
19 1.6239024051837192e-47  -  15.034692584456996
20 1.206292442092121e-46  -  14.20677968101732
21 1.7158469520

### *** Features exógenas con mejor valor de Causalidad Granger

In [36]:
selectedLaggedfeatures

[['COTA_EMBALSE_diff', 1],
 ['COTA_RESTITUCION_diff', 1],
 ['QAFLR_diff', 5],
 ['QVBP_diff', 1],
 ['QVBAC_diff', 1],
 ['QTURB_diff', 2],
 ['SINP_diff', 1],
 ['SADI_diff', 2]]

### Feature Engineering

### Variables exógenas

In [37]:
# Variables exógenas
for laggedFeature in selectedLaggedfeatures:
    df[laggedFeature[0] + '-' + str(laggedFeature[1]).zfill(2)] = ds[laggedFeature[0]].shift(periods=laggedFeature[1])

##### Genero los lags (hasta 99)

In [38]:
lags = 60
for i in range(1, lags+1):
    df['SALTO-' + str(i).zfill(2)] = df['SALTO'].shift(periods=i)

####  Borro los registros que quedaron con un NAN al desplazarse

In [39]:
df.dropna(how='any', inplace=True)

#### Imprio el conjunto completo de las features

In [40]:
df.columns

Index(['COTA_EMBALSE', 'COTA_RESTITUCION', 'SALTO', 'QAFLR', 'QVBP', 'QVBAC',
       'QTURB', 'SINP', 'SADI', 'COTA_EMBALSE_diff-01',
       'COTA_RESTITUCION_diff-01', 'QAFLR_diff-05', 'QVBP_diff-01',
       'QVBAC_diff-01', 'QTURB_diff-02', 'SINP_diff-01', 'SADI_diff-02',
       'SALTO-01', 'SALTO-02', 'SALTO-03', 'SALTO-04', 'SALTO-05', 'SALTO-06',
       'SALTO-07', 'SALTO-08', 'SALTO-09', 'SALTO-10', 'SALTO-11', 'SALTO-12',
       'SALTO-13', 'SALTO-14', 'SALTO-15', 'SALTO-16', 'SALTO-17', 'SALTO-18',
       'SALTO-19', 'SALTO-20', 'SALTO-21', 'SALTO-22', 'SALTO-23', 'SALTO-24',
       'SALTO-25', 'SALTO-26', 'SALTO-27', 'SALTO-28', 'SALTO-29', 'SALTO-30',
       'SALTO-31', 'SALTO-32', 'SALTO-33', 'SALTO-34', 'SALTO-35', 'SALTO-36',
       'SALTO-37', 'SALTO-38', 'SALTO-39', 'SALTO-40'],
      dtype='object')

In [41]:
# Consolido las features exógenas diferenciadas y las generadas con lags en un solo conjunto
features_completo = [col for col in df.columns if col[0:5] == 'SALTO'] + [col for col in df.columns if '_diff' in col] 

In [42]:
features_completo

['SALTO',
 'SALTO-01',
 'SALTO-02',
 'SALTO-03',
 'SALTO-04',
 'SALTO-05',
 'SALTO-06',
 'SALTO-07',
 'SALTO-08',
 'SALTO-09',
 'SALTO-10',
 'SALTO-11',
 'SALTO-12',
 'SALTO-13',
 'SALTO-14',
 'SALTO-15',
 'SALTO-16',
 'SALTO-17',
 'SALTO-18',
 'SALTO-19',
 'SALTO-20',
 'SALTO-21',
 'SALTO-22',
 'SALTO-23',
 'SALTO-24',
 'SALTO-25',
 'SALTO-26',
 'SALTO-27',
 'SALTO-28',
 'SALTO-29',
 'SALTO-30',
 'SALTO-31',
 'SALTO-32',
 'SALTO-33',
 'SALTO-34',
 'SALTO-35',
 'SALTO-36',
 'SALTO-37',
 'SALTO-38',
 'SALTO-39',
 'SALTO-40',
 'COTA_EMBALSE_diff-01',
 'COTA_RESTITUCION_diff-01',
 'QAFLR_diff-05',
 'QVBP_diff-01',
 'QVBAC_diff-01',
 'QTURB_diff-02',
 'SINP_diff-01',
 'SADI_diff-02']

In [43]:
df.columns

Index(['COTA_EMBALSE', 'COTA_RESTITUCION', 'SALTO', 'QAFLR', 'QVBP', 'QVBAC',
       'QTURB', 'SINP', 'SADI', 'COTA_EMBALSE_diff-01',
       'COTA_RESTITUCION_diff-01', 'QAFLR_diff-05', 'QVBP_diff-01',
       'QVBAC_diff-01', 'QTURB_diff-02', 'SINP_diff-01', 'SADI_diff-02',
       'SALTO-01', 'SALTO-02', 'SALTO-03', 'SALTO-04', 'SALTO-05', 'SALTO-06',
       'SALTO-07', 'SALTO-08', 'SALTO-09', 'SALTO-10', 'SALTO-11', 'SALTO-12',
       'SALTO-13', 'SALTO-14', 'SALTO-15', 'SALTO-16', 'SALTO-17', 'SALTO-18',
       'SALTO-19', 'SALTO-20', 'SALTO-21', 'SALTO-22', 'SALTO-23', 'SALTO-24',
       'SALTO-25', 'SALTO-26', 'SALTO-27', 'SALTO-28', 'SALTO-29', 'SALTO-30',
       'SALTO-31', 'SALTO-32', 'SALTO-33', 'SALTO-34', 'SALTO-35', 'SALTO-36',
       'SALTO-37', 'SALTO-38', 'SALTO-39', 'SALTO-40'],
      dtype='object')

### Límites del dataset

In [44]:
print('\n*** El dataset queda desde: ', df.index[0].strftime('%Y-%m-%d'), ', hasta: ', df.index[-1].strftime('%Y-%m-%d'))  


*** El dataset queda desde:  2011-02-10 , hasta:  2021-06-30


### Conjunto de regresores a utilizar

In [45]:
# Lista con los regresores
regresores = [ 
    KNeighborsRegressor()
    ,Lasso()
    ,LGBMRegressor(objective='regression', linear_tree=True)
    ,LinearRegression()
    ,MLPRegressor(max_iter=600, random_state=170162)
    ,RandomForestRegressor(criterion='absolute_error', random_state=170162) 
    ,Ridge()
    ,SVR(gamma='auto', kernel='rbf') 
    ,XGBRegressor()
    ]

### Métricas de evaluación de desempeño

In [46]:
mae = MeanAbsoluteError()
mse = MeanSquaredError()
rmse = MeanSquaredError(square_root=True)
mase = MeanAbsoluteScaledError()

### Conjuntos de Predictoras y de Target

#### Matriz de predictoras "X" 

In [47]:
# Me quedo con las columnas del df menos 'SALTO'
X = df[features_completo].drop(columns=['SALTO'])

In [48]:
X.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 3794 entries, 2011-02-10 to 2021-06-30
Freq: D
Data columns (total 48 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   SALTO-01                  3794 non-null   float64
 1   SALTO-02                  3794 non-null   float64
 2   SALTO-03                  3794 non-null   float64
 3   SALTO-04                  3794 non-null   float64
 4   SALTO-05                  3794 non-null   float64
 5   SALTO-06                  3794 non-null   float64
 6   SALTO-07                  3794 non-null   float64
 7   SALTO-08                  3794 non-null   float64
 8   SALTO-09                  3794 non-null   float64
 9   SALTO-10                  3794 non-null   float64
 10  SALTO-11                  3794 non-null   float64
 11  SALTO-12                  3794 non-null   float64
 12  SALTO-13                  3794 non-null   float64
 13  SALTO-14                  3794 non-nu

#### Vector de Target

In [49]:
# Quedo con todas las columnas de df menos las de X (da 'SALTO')
y = df.drop(columns=X.columns)

# Quito las variables exógenas originales
y = y.drop(columns=features_exogenas)

In [50]:
y.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 3794 entries, 2011-02-10 to 2021-06-30
Freq: D
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   SALTO   3794 non-null   float64
dtypes: float64(1)
memory usage: 59.3 KB


#### Lista de métricas

In [51]:
# Lista para las métricas
metricas = []

#### Dataframe de pronósticos (y_preds)

In [52]:
y_preds_df = pd.DataFrame()

### Parámetros para los lazos de 'fh' y de nro. de 'lags'

#### Conjunto de variables (lags) a utilizar

In [53]:
# Conjunto con los números de lags a utilizar
lags_s = [40, 30, 20, 10]

#### Conjunto de horizontes de pronóstico

In [54]:
# Horizontes de predicción a explorar
fh_s = [56, 28, 14, 7]

### Lazo principal

In [55]:
# Lazo de horizontes de predicción
for fh in fh_s:
    
    # Impresión de control
    print('\nProcesando horizonte de ', fh, ' días')
    
    # Lazo de lags
    for lags in lags_s:
        
        #### Lista de modelos
        modelos = []
        
        # Impresión de control
        print('\nProcesando lags de ', lags, ' variables')
        
        # Selecciono las columnas a usar de la matriz de predictoras 'X'
        features_diff = [col for col in df.columns if '_diff' in col]
        features_lags = [col for col in X.columns if (col[0:6]=='SALTO-' and int(col[6:8]) <= lags)] # Agrego variables del dataset
        
        # Me quedo con las pdictoras correspondientes al lags en proceso 
        X_features = X[features_diff + features_lags]
        
#         print('\nMatriz X_features:')
#         X_features.info()
        
        ### Puntos de testing (x fh) a reservar
        # Nro de puntos de prueba
        t = 1

        # Cantidad de registros a reservar
        nTesting = t * fh

        ### Conjuntos de Training y de Testing

        #### Training
        X_train = X_features.iloc[0:-nTesting,]
        y_train = y.iloc[0:-nTesting,]

#         # Imprimo info de los conjuntos de training
#         print('\nMatriz X_train:')
#         X_train.info()
#         print('\nVector y_train:')
#         y_train.info()

        #### Testing
        X_test = X_features.iloc[-nTesting:,]
        y_test = y.iloc[-nTesting:,]

#         # Imprimo info de los conjuntos de test
#         print('\nMatriz X_test:')
#         X_test.info()
#         print('\nVector y_test:')
#         y_test.info()
        
        ### Entrenamiento / ajuste de los modelos
        print('\nAjuste de modelos...')

        # Ciclo la lista de regresores
        for regre in regresores:

            # Impresión de Control
            print('\nRegresor: ', type(regre).__name__)

            # Lista para los modelos diarios (submodelos)
            submodelos = []

            for dia in range(0, fh):

                # Reseteo el regresor seleccionado
                regresor = clone(regre)

                # Impresión de Control
                print('Ajustando día', dia)

                # Conjuntos de entrenamiento
                y_train_submodelo = y_train.shift(periods=-dia).iloc[0:(-1-dia)]
                X_train_submodelo = X_train.iloc[0:(-1-dia)]

        #         print(X_train_submodelo.info(), y_train_submodelo.info())

                # Ajusto un modelo y lo agrego a la lista de submodelos
                submodelos.append(regresor.fit(X_train_submodelo, y_train_submodelo.values.ravel()))

                # *** Fin lazo de los días

            # Agrego la lista de submodelos a la lista de modelos
            modelos.append(
                {'regresor': type(regresor).__name__
                 ,'lags':lags
                 ,'fh': fh
                 ,'submodelos': submodelos}
                )

            # *** Fin lazo regresores  

        # Impresión de control
        print('\nFin ajuste de modelos.')   
         
        ### Pronóstico / predicciones

        #### Calculo x_pred, como la primera fila de X_test
        x_pred = X_test.iloc[0:1]

        # Guardo y_test en el dataframe de predicciones
        y_preds_df[str(fh) + '_' + str(lags) + '_' + 'y_test'] = y_test

        # Impresión de control
        print('\nPredicción de valores...')

        # Ciclo los modelos ajustados
        for modelo in modelos:

            # Impresión de Control
            print('\nPrediciendo Regresor: ', modelo['regresor'])

            # Lista para las predicciones diarias de cada submodelo
            y_pred = []

            for dia in range(0, fh):

                # Impresión de Control
                print('Prediciendo día:', dia, ', Valor:', modelo['submodelos'][dia].predict(x_pred)[0])

                # Predigo y agrego a la lista de y_pred
                y_pred.append(modelo['submodelos'][dia].predict(x_pred)[0])

                # *** Fin lazo de los días

            # Convierto la lista de predicciones a una serie
            y_pred_series = pd.Series(y_pred, index = y_test.index)

            # Agrego la predicción al dataframe de predicciones
            y_preds_df[str(fh)+'_' + str(lags) + '_' + modelo['regresor']] = y_pred_series

            # Calculo metricas
            MAE = mae(y_test, y_pred_series) 
            MSE = mse(y_test, y_pred_series)
            RMSE = rmse(y_true=y_test, y_pred=y_pred_series) 
            MASE = mase(y_true=y_test, y_pred=y_pred_series, y_train=y_train)

            metricas.append({'fh': fh
                             ,'lags':lags
                             ,'regresor': modelo['regresor']
                             ,'MAE': MAE
                             ,'MSE': MSE
                             ,'RMSE': RMSE
                             ,'MASE': MASE
                            })

            # *** Fin lazo modelos

            # Ploteo los resultados del regresor/lags
            pd.concat([y.iloc[-(fh+5):], y_pred_series.to_frame(name='SALTO_pred')], axis=1).iplot(
                mode='lines+markers', size=5.0
                ,title='Algoritmo: ' + modelo['regresor']  + ',  features: ' + str(lags) + ',  fh:'+ str(fh) + ', MAE: ' + f'{MAE:0.4f}' + ', RMSE: ' + f'{RMSE:0.4f}'
                ,yTitle='metros'
                ,xTitle='Fecha'
                ,dimensions=(950, 350)
                )


        # Impresión de control
        print('\nFin predicción.')  
        
    
    # Impresión de control
    print('\nFin procesamiento de lags.')
    
    
    
    # *** Fin lazo horizones
    
# Impresión de control
print('\nFin procesamiento de horizontes')


Procesando horizonte de  56  días

Procesando lags de  40  variables

Ajuste de modelos...

Regresor:  KNeighborsRegressor
Ajustando día 0
Ajustando día 1
Ajustando día 2
Ajustando día 3
Ajustando día 4
Ajustando día 5
Ajustando día 6
Ajustando día 7
Ajustando día 8
Ajustando día 9
Ajustando día 10
Ajustando día 11
Ajustando día 12
Ajustando día 13
Ajustando día 14
Ajustando día 15
Ajustando día 16
Ajustando día 17
Ajustando día 18
Ajustando día 19
Ajustando día 20
Ajustando día 21
Ajustando día 22
Ajustando día 23
Ajustando día 24
Ajustando día 25
Ajustando día 26
Ajustando día 27
Ajustando día 28
Ajustando día 29
Ajustando día 30
Ajustando día 31
Ajustando día 32
Ajustando día 33
Ajustando día 34
Ajustando día 35
Ajustando día 36
Ajustando día 37
Ajustando día 38
Ajustando día 39
Ajustando día 40
Ajustando día 41
Ajustando día 42
Ajustando día 43
Ajustando día 44
Ajustando día 45
Ajustando día 46
Ajustando día 47
Ajustando día 48
Ajustando día 49
Ajustando día 50
Ajustando día 51
Aj

Ajustando día 21
Ajustando día 22
Ajustando día 23
Ajustando día 24
Ajustando día 25
Ajustando día 26
Ajustando día 27
Ajustando día 28
Ajustando día 29
Ajustando día 30
Ajustando día 31
Ajustando día 32
Ajustando día 33
Ajustando día 34
Ajustando día 35
Ajustando día 36
Ajustando día 37
Ajustando día 38
Ajustando día 39
Ajustando día 40
Ajustando día 41
Ajustando día 42
Ajustando día 43
Ajustando día 44
Ajustando día 45
Ajustando día 46
Ajustando día 47
Ajustando día 48
Ajustando día 49
Ajustando día 50
Ajustando día 51
Ajustando día 52
Ajustando día 53
Ajustando día 54
Ajustando día 55

Fin ajuste de modelos.

Predicción de valores...

Prediciendo Regresor:  KNeighborsRegressor
Prediciendo día: 0 , Valor: 23.35
Prediciendo día: 1 , Valor: 23.366
Prediciendo día: 2 , Valor: 23.292
Prediciendo día: 3 , Valor: 23.266000000000002
Prediciendo día: 4 , Valor: 23.259999999999998
Prediciendo día: 5 , Valor: 23.258
Prediciendo día: 6 , Valor: 23.302
Prediciendo día: 7 , Valor: 23.355999999999


Prediciendo Regresor:  Lasso
Prediciendo día: 0 , Valor: 22.937931559711426
Prediciendo día: 1 , Valor: 22.943424916656607
Prediciendo día: 2 , Valor: 22.946030779313677
Prediciendo día: 3 , Valor: 22.945606419324037
Prediciendo día: 4 , Valor: 22.941580113022074
Prediciendo día: 5 , Valor: 22.937374628142265
Prediciendo día: 6 , Valor: 22.93941631188084
Prediciendo día: 7 , Valor: 22.940132492191093
Prediciendo día: 8 , Valor: 22.942816440627695
Prediciendo día: 9 , Valor: 22.94310025788241
Prediciendo día: 10 , Valor: 22.941328703660066
Prediciendo día: 11 , Valor: 22.938310632240295
Prediciendo día: 12 , Valor: 22.93408065691836
Prediciendo día: 13 , Valor: 22.93545401021076
Prediciendo día: 14 , Valor: 22.93877348507337
Prediciendo día: 15 , Valor: 22.943351331037682
Prediciendo día: 16 , Valor: 22.946069673542954
Prediciendo día: 17 , Valor: 22.94671362040288
Prediciendo día: 18 , Valor: 22.941437894841293
Prediciendo día: 19 , Valor: 22.936632502954403
Prediciendo día: 20 , Valo


Prediciendo Regresor:  LGBMRegressor
Prediciendo día: 0 , Valor: 23.73688335584048
Prediciendo día: 1 , Valor: 23.677530864420884
Prediciendo día: 2 , Valor: 23.661435762639968
Prediciendo día: 3 , Valor: 23.646293172151605
Prediciendo día: 4 , Valor: 23.423756143933915
Prediciendo día: 5 , Valor: 23.477458364356046
Prediciendo día: 6 , Valor: 23.55706397583921
Prediciendo día: 7 , Valor: 23.507273816342444
Prediciendo día: 8 , Valor: 23.49758092689673
Prediciendo día: 9 , Valor: 23.364505000325863
Prediciendo día: 10 , Valor: 23.44662250210589
Prediciendo día: 11 , Valor: 23.474460414122067
Prediciendo día: 12 , Valor: 23.673334218563735
Prediciendo día: 13 , Valor: 23.534275101387053
Prediciendo día: 14 , Valor: 23.467031689247186
Prediciendo día: 15 , Valor: 23.567310175025042
Prediciendo día: 16 , Valor: 23.476648587243165
Prediciendo día: 17 , Valor: 23.540193405648196
Prediciendo día: 18 , Valor: 23.36339507086172
Prediciendo día: 19 , Valor: 23.563247361305734
Prediciendo día: 


Prediciendo Regresor:  LinearRegression
Prediciendo día: 0 , Valor: 23.749199083925802
Prediciendo día: 1 , Valor: 23.721692649081426
Prediciendo día: 2 , Valor: 23.704185591313948
Prediciendo día: 3 , Valor: 23.687609400451322
Prediciendo día: 4 , Valor: 23.647387292899793
Prediciendo día: 5 , Valor: 23.611429741650692
Prediciendo día: 6 , Valor: 23.585470275251133
Prediciendo día: 7 , Valor: 23.56934662907541
Prediciendo día: 8 , Valor: 23.562191385692483
Prediciendo día: 9 , Valor: 23.564310820698957
Prediciendo día: 10 , Valor: 23.54414231012073
Prediciendo día: 11 , Valor: 23.50732950855864
Prediciendo día: 12 , Valor: 23.480267290117553
Prediciendo día: 13 , Valor: 23.447429410638975
Prediciendo día: 14 , Valor: 23.455419770488042
Prediciendo día: 15 , Valor: 23.47500228365682
Prediciendo día: 16 , Valor: 23.496490020861636
Prediciendo día: 17 , Valor: 23.488189365550394
Prediciendo día: 18 , Valor: 23.450322812009894
Prediciendo día: 19 , Valor: 23.41901031179912
Prediciendo dí

...


Prediciendo Regresor:  SVR
Prediciendo día: 0 , Valor: 22.941188163689382
Prediciendo día: 1 , Valor: 22.941569503821384
Prediciendo día: 2 , Valor: 22.941896708137712
Prediciendo día: 3 , Valor: 22.942216387915416
Prediciendo día: 4 , Valor: 22.94256355382526
Prediciendo día: 5 , Valor: 22.94294991566045
Prediciendo día: 6 , Valor: 22.94333917218019


C:\Users\josel\AppData\Local\Temp/ipykernel_8392/16749489.py:133: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`




Prediciendo Regresor:  XGBRegressor
Prediciendo día: 0 , Valor: 23.78571
Prediciendo día: 1 , Valor: 23.57002
Prediciendo día: 2 , Valor: 23.64062
Prediciendo día: 3 , Valor: 23.488583
Prediciendo día: 4 , Valor: 23.52878
Prediciendo día: 5 , Valor: 23.529682
Prediciendo día: 6 , Valor: 23.617065


C:\Users\josel\AppData\Local\Temp/ipykernel_8392/16749489.py:133: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`




Fin predicción.

Fin procesamiento de lags.

Fin procesamiento de horizontes


In [56]:
# Guardo el dataframe de predicciones en disco
y_preds_df.to_csv(path_grabacion + 'y_preds_df.csv')

In [57]:
y_preds_df.iplot()

### Análisis de las métricas

In [58]:
# Creo un dataframe con la lista de métricas
metricas_df = pd.DataFrame(metricas)

In [59]:
# Guardo el dataframe de metricas en disco
metricas_df.to_csv(path_grabacion + 'metricas_df.csv', index=False)

In [60]:
metricas_df.sort_values('MAE').style.set_properties(**{'text-align': 'left'}).hide_index()

#### Mínimos MAE

In [61]:
# Listo las combinaciones regresor/lags para el horizonte de pronóstico de 48 días 
metricas_df.loc[metricas_df['fh']==7].sort_values(['fh', 'MAE'])

fh  lags               regresor       MAE       MSE      RMSE       MASE
114   7    40                  Ridge  0.125003  0.016652  0.129043   1.644814
111   7    40       LinearRegression  0.126541  0.017044  0.130551   1.665046
123   7    30                  Ridge  0.137421  0.019977  0.141339   1.808213
120   7    30       LinearRegression  0.138863  0.020387  0.142784   1.827179
132   7    20                  Ridge  0.138977  0.023302  0.152650   1.828689
129   7    20       LinearRegression  0.140762  0.023837  0.154391   1.852167
141   7    10                  Ridge  0.142570  0.024540  0.156653   1.875955
138   7    10       LinearRegression  0.144043  0.025017  0.158167   1.895340
116   7    40           XGBRegressor  0.170542  0.044525  0.211009   2.244015
140   7    10  RandomForestRegressor  0.175836  0.038403  0.195968   2.313676
128   7    20          LGBMRegressor  0.178836  0.037619  0.193956   2.353150
131   7    20  RandomForestRegressor  0.183057  0.037901  0.194683   2.408697
134   7    20           XGBRegressor  0.188941  0.043592  0.208787   2.486117
113   7    40  RandomForestRegressor  0.190429  0.040357  0.200891   2.505691
137   7    10          LGBMRegressor  0.201416  0.046398  0.215402   2.650268
122   7    30  RandomForestRegressor  0.204329  0.046690  0.216078   2.688590
125   7    30           XGBRegressor  0.210950  0.058625  0.242127   2.775713
119   7    30          LGBMRegressor  0.223266  0.053316  0.230902   2.937768
110   7    40          LGBMRegressor  0.245521  0.069267  0.263186   3.230609
143   7    10           XGBRegressor  0.259934  0.076842  0.277204   3.420260
108   7    40    KNeighborsRegressor  0.566000  0.323446  0.568723   7.447524
117   7    30    KNeighborsRegressor  0.566000  0.323446  0.568723   7.447524
126   7    20    KNeighborsRegressor  0.566000  0.323446  0.568723   7.447524
135   7    10    KNeighborsRegressor  0.566000  0.323446  0.568723   7.447524
130   7    20           MLPRegressor  0.693238  0.739230  0.859785   9.121743
142   7    10                    SVR  0.912040  0.832079  0.912183  12.000770
133   7    20                    SVR  0.912040  0.832079  0.912183  12.000770
124   7    30                    SVR  0.912040  0.832079  0.912183  12.000770
115   7    40                    SVR  0.912040  0.832079  0.912183  12.000770
109   7    40                  Lasso  0.915700  0.838707  0.915810  12.048941
118   7    30                  Lasso  0.915700  0.838707  0.915810  12.048941
127   7    20                  Lasso  0.915700  0.838707  0.915810  12.048941
136   7    10                  Lasso  0.915700  0.838707  0.915810  12.048941
139   7    10           MLPRegressor  1.063885  1.440107  1.200045  13.998774
121   7    30           MLPRegressor  1.769101  3.615332  1.901403  23.278135
112   7    40           MLPRegressor  1.881655  4.550659  2.133227  24.759131

#### Desempeño de cada regresor

In [62]:
for lags in lags_s:
    metricas_df.loc[metricas_df['lags']==lags].sort_values(by=['fh', 'MAE']).iplot(kind='bar'
                                         ,x=['fh', 'regresor']
                                         ,y=['MAE', 'RMSE']
                                         ,title='Desempeño de cada regresor, por horizonte de predicción y nro. de lags a '+ str(fh) + ' días y con ' + str(lags) + ' variables' 
                                         ,yTitle='metros', xTitle='Regresor'
                                         ,dimensions=(950, 500)
                                         ,theme='pearl'
                                        )

In [63]:
# Pivoteo el dataframe de métricas, para agrupar los MAE por nro. de lags
metricas_df.pivot_table(index=['fh', 'lags'], columns='regresor', values='MAE')

regresor  KNeighborsRegressor  LGBMRegressor     Lasso  LinearRegression  \
fh lags                                                                    
7  10                0.566000       0.201416  0.915700          0.144043   
   20                0.566000       0.178836  0.915700          0.140762   
   30                0.566000       0.223266  0.915700          0.138863   
   40                0.566000       0.245521  0.915700          0.126541   
14 10                0.742571       0.104597  0.873621          0.227515   
   20                0.742571       0.115859  0.873621          0.244556   
   30                0.742571       0.133210  0.873621          0.195888   
   40                0.742571       0.139400  0.873621          0.174976   
28 10                0.642143       0.278609  0.805919          0.259934   
   20                0.642143       0.211778  0.805919          0.235927   
   30                0.642143       0.210416  0.805919          0.211342   
   40                0.642143       0.200651  0.805919          0.201003   
56 10                0.643714       0.359977  0.787078          0.382217   
   20                0.643714       0.347497  0.787078          0.359927   
   30                0.643714       0.271625  0.787078          0.358340   
   40                0.643714       0.220546  0.787078          0.357212   

regresor  MLPRegressor  RandomForestRegressor     Ridge       SVR  \
fh lags                                                             
7  10         1.063885               0.175836  0.142570  0.912040   
   20         0.693238               0.183057  0.138977  0.912040   
   30         1.769101               0.204329  0.137421  0.912040   
   40         1.881655               0.190429  0.125003  0.912040   
14 10         0.593672               0.129286  0.227414  0.872702   
   20         1.618295               0.140543  0.244157  0.872702   
   30         1.326550               0.139971  0.195865  0.872702   
   40         1.115047               0.154264  0.175089  0.872702   
28 10         3.385390               0.432036  0.260447  0.857438   
   20         2.589014               0.376054  0.236449  0.857438   
   30         2.329447               0.361175  0.211906  0.857438   
   40         3.406708               0.380304  0.201603  0.857438   
56 10         1.528822               0.373233  0.381655  0.794642   
   20         0.946815               0.378716  0.359510  0.794642   
   30         1.225508               0.360407  0.357980  0.794642   
   40         1.167752               0.342159  0.356921  0.794642   

regresor  XGBRegressor  
fh lags                 
7  10         0.259934  
   20         0.188941  
   30         0.210950  
   40         0.170542  
14 10         0.106663  
   20         0.111166  
   30         0.107772  
   40         0.131293  
28 10         0.415707  
   20         0.294337  
   30         0.309328  
   40         0.424473  
56 10         0.404305  
   20         0.463773  
   30         0.453154  
   40         0.409718

#### Máximos, promedio y mínimos MAE por cada horizonte y número de lags

In [64]:
# Ploteo el mínimo MAE por cada nro. de lags
metricas_df.groupby(['fh', 'lags'])['MAE'].agg(['max', 'mean', 'min']).iplot(kind='bar'
                                                 ,title='MAE (máximo, promedio y mínimo), por horizonte de pronóstico y por número de features (lags)' 
                                                 ,yTitle='metros'
                                                 , xTitle='(horizonte de pronóstico, nro. de lags)'
                                                 ,dimensions=(950, 350)
                                                 ,theme='pearl'
                                                )

In [65]:
# Ploteo los MAE por nro de lags y por regresor
metricas_df.iplot(kind='bar'
                  ,x=['fh', 'lags', 'regresor']
                  ,y=['MAE']
                  ,title='MAE de cada regresor, por horizonte de pronóstico y por número de features (lags)' 
                  ,yTitle='metros'
                  ,xTitle='(horizonte de pronóstico, nro. de lags, regresor)'
                  ,dimensions=(950, 700)
                  ,theme='pearl'
                  ,barmode='group'
                  )

In [66]:
# Pivoteo el dataframe de métricas, para agrupar los MAE por nro. de lags
metricas_df.pivot_table(index=['fh', 'lags'], columns='regresor', values='MAE')

regresor  KNeighborsRegressor  LGBMRegressor     Lasso  LinearRegression  \
fh lags                                                                    
7  10                0.566000       0.201416  0.915700          0.144043   
   20                0.566000       0.178836  0.915700          0.140762   
   30                0.566000       0.223266  0.915700          0.138863   
   40                0.566000       0.245521  0.915700          0.126541   
14 10                0.742571       0.104597  0.873621          0.227515   
   20                0.742571       0.115859  0.873621          0.244556   
   30                0.742571       0.133210  0.873621          0.195888   
   40                0.742571       0.139400  0.873621          0.174976   
28 10                0.642143       0.278609  0.805919          0.259934   
   20                0.642143       0.211778  0.805919          0.235927   
   30                0.642143       0.210416  0.805919          0.211342   
   40                0.642143       0.200651  0.805919          0.201003   
56 10                0.643714       0.359977  0.787078          0.382217   
   20                0.643714       0.347497  0.787078          0.359927   
   30                0.643714       0.271625  0.787078          0.358340   
   40                0.643714       0.220546  0.787078          0.357212   

regresor  MLPRegressor  RandomForestRegressor     Ridge       SVR  \
fh lags                                                             
7  10         1.063885               0.175836  0.142570  0.912040   
   20         0.693238               0.183057  0.138977  0.912040   
   30         1.769101               0.204329  0.137421  0.912040   
   40         1.881655               0.190429  0.125003  0.912040   
14 10         0.593672               0.129286  0.227414  0.872702   
   20         1.618295               0.140543  0.244157  0.872702   
   30         1.326550               0.139971  0.195865  0.872702   
   40         1.115047               0.154264  0.175089  0.872702   
28 10         3.385390               0.432036  0.260447  0.857438   
   20         2.589014               0.376054  0.236449  0.857438   
   30         2.329447               0.361175  0.211906  0.857438   
   40         3.406708               0.380304  0.201603  0.857438   
56 10         1.528822               0.373233  0.381655  0.794642   
   20         0.946815               0.378716  0.359510  0.794642   
   30         1.225508               0.360407  0.357980  0.794642   
   40         1.167752               0.342159  0.356921  0.794642   

regresor  XGBRegressor  
fh lags                 
7  10         0.259934  
   20         0.188941  
   30         0.210950  
   40         0.170542  
14 10         0.106663  
   20         0.111166  
   30         0.107772  
   40         0.131293  
28 10         0.415707  
   20         0.294337  
   30         0.309328  
   40         0.424473  
56 10         0.404305  
   20         0.463773  
   30         0.453154  
   40         0.409718

#### MAE de cada regresor por horizonte y por conjunto de lags

In [67]:
# Ploteo los MAE para cada regresor, para cada nro. de lags
metricas_df.pivot_table(index=['fh', 'lags'], columns='regresor', values='MAE').iplot(kind='bar'
                                                                              ,title='MAE de cada regresor, por número de features (lags)'
                                                                              ,yTitle='metros'
                                                                              ,xTitle='(horizonde de pronóstico, nro. de lags)'
                                                                              ,dimensions=(950, 350)
                                                                              ,theme='pearl'
                                                                              )

In [68]:
# Busco el mínimo MAE
metricas_df[metricas_df['MAE']==metricas_df['MAE'].min()]

fh  lags       regresor       MAE       MSE      RMSE      MASE
101  14    10  LGBMRegressor  0.104597  0.016028  0.126602  1.374572

In [69]:
# Busco el mínimo MAE
for fh in fh_s:
    metricas_df_fh = metricas_df[metricas_df['fh']==fh]
    print(metricas_df_fh[metricas_df_fh['MAE']==metricas_df_fh['MAE'].min()])

   fh  lags       regresor       MAE       MSE      RMSE      MASE
2  56    40  LGBMRegressor  0.220546  0.066478  0.257833  2.892672
    fh  lags       regresor       MAE       MSE      RMSE      MASE
38  28    40  LGBMRegressor  0.200651  0.054775  0.234041  2.631496
     fh  lags       regresor       MAE       MSE      RMSE      MASE
101  14    10  LGBMRegressor  0.104597  0.016028  0.126602  1.374572
     fh  lags regresor       MAE       MSE      RMSE      MASE
114   7    40    Ridge  0.125003  0.016652  0.129043  1.644814


## Fin

In [70]:
print('\n¡FIN!', '(al fin.....)')


¡FIN! (al fin.....)
